# Transfer HTTP (Push)

With this notebook you can transfer data from an offer for which you already have an Agreement to an `HTTP` endpoint.

## Preperation

Here some values are initialized that will be necessary for the other steps.


### Set up

Import the requests module and assign the base url of the Dataspace as a variable.

In [ ]:
from pprint import pprint
import requests

base_url = "https://api.adsel.space"

### Fill in Values

Fill in the values for the variables below.

In [ ]:
# Your JWT recevied from Keycloak via sso.adsel.space
token = "ey..."
token_header = {"Authorization": f"Bearer {token}"}
# The name of your Connector
connector_name = "my-connector"
# The URL of your endpoint where the data should be sent to
endpoint_url = "https://my-endpoint.requestcatcher.com"
# The DSP address of the Connector providing the offer
originator = "https://api.adsel.space/connectors/alice/dsp"
# The ID of the Agreement for the offer
agreement_id = "some-random-uuid"

## Initiate Transfer

Here you will request for the transfer of the data to your endpoint.

Initiates the transfer.

In [ ]:
url = f"{base_url}/connectors/{connector_name}/management/v3/transferprocesses"
payload = {
  "@context": {
    "odrl": "http://www.w3.org/ns/odrl/2/"
  },
  "counterPartyAddress": originator,
  "contractId": agreement_id,
  "transferType": "HttpData-PUSH",
  "dataDestination": {
    "type": "HttpData",
    "baseUrl": endpoint_url,
  },
  "protocol": "dataspace-protocol-http"
}

response = requests.post(url, json=payload, headers=token_header)
print(response.content)
response.raise_for_status()

transfer_id = response.json()["@id"]
print(f"Started Transfer with ID: {transfer_id}")

Confirms that the transfer succeeded.

In [ ]:
url = f"{base_url}/connectors/{connector_name}/management/v3/transferprocesses/{transfer_id}"

response = requests.get(url, headers=token_header)
response.raise_for_status()
print(f"Transfer data:\n")
pprint(response.json())

If everything was successful the data should now have been sent to your endpoint.